In [3]:
import math
import numpy as np
import re
import argparse
import os
import glob
from pathlib import Path
import unidecode
import time
import unicodedata

In [38]:
#Recebendo e atribuindo os argumentos

#Argumentos funcionam apenas em executáveis .py, portanto o código deve ser descomentado quando o código for exportado.

# parser = argparse.ArgumentParser()
# parser.add_argument("dataset", help="O banco de dados no qual será realizada a pesquisa. Deve ser uma pasta.")
# args   = parser.parse_args()


In [4]:
#Parâmetro: Um dicionário, contendo como chave o código do documento e como valor o texto "bruto" do documento, 
    #sem formatações, 
#Retorno: Um dicionário, contendo como chave o código do documento e como valor o texto formatado do documento,
    #sem acentuações, caracteres especiais e letras que não estão no Padrão ASCII, com todas as letras são minúsculas e
    #separadas por espaço " " e armazenadas em um vetor
def formataString (s):
#   Parte substituída por Regex    
#     caracteresEspeciais = ['!', '\"', '#', '$', '%', '&', '\'', '(', ')', '*', '+', ',', '-', '.', '/', ':', ';', '<', '=', '>',
#                            '?', '@', '[', '\\', ']', '^', '_', '`', '{', '|', '}', '~']
#     for carac in caracteresEspeciais:
#         if (s.count(carac) > 0):
#             s = s.replace(carac, "")

    s = s.lower()
    
    #Removendo tudo que não é letra minúscula, número ou espaço.
    s = re.sub("[:,'|.@()?!#$&]"," ", s)
    s = s.replace("\n", " ")
    s = re.sub('[^A-Za-z0-9 ]+', '', s)
    
    strings = s.split()
    
    return strings

In [5]:
def indiceInvertido (arquivos):
    vocabulario = []

    for k, v in arquivos.items():
        #print(k, " : ", v)

        ignorarIndice = []
        for i in range(len(v)):
            frequenciaNesteDoc = 1
            if (ignorarIndice.count(i) != 0):
                continue

            for j in range(i+1, len(v)):
                if (v[i] == v[j]):
                    frequenciaNesteDoc+=1
                    ignorarIndice.append(j)

            vocabulario.append([v[i], k, frequenciaNesteDoc])

    #print("Vocabulário:")
    #for val in vocabulario:
    #    print(val[0], " -> ", val[1], " : ", val[2])
    #print()
    
    ############################################################ TODO: Separar essas funções?
    
    indInv = {}

    for val in vocabulario:
        if val[0] in indInv.keys():
            dados = indInv[val[0]]
            dados.append([val[1], val[2]])
            indInv[val[0]] = dados
        else:
            dados = [[val[1],val[2]]]
            indInv[val[0]] = dados

    #print("A palavra em questão -> [Os documentos em que ela aparece, a quantidade total que ela aparece nesse doc]")
    #for k, v in indInv.items():
    #    print(k, "-> ", v)
        
    #############################################################
        
    return indInv

In [6]:
def coordenadas (indInv, numDocs):
    coords = np.zeros((len(indInv), numDocs))
    indicePalavra = 0;
    
    for k, v in indInv.items():
        nx = len(v)
        idf = math.log(numDocs/nx)
        #print(idf)
        for dados in v:
            w = dados[1] * idf
            coords[indicePalavra][dados[0]] = w
        
        indicePalavra+=1
        
    return coords

In [7]:
def formataQuery (indInv, indQ, numDocs):
    Q = np.zeros((len(indInv),1))
    indicePalavra = 0;
    
    for k, v in indInv.items():
        if k in indQ.keys():
            nx = len(v)
            idf = math.log(numDocs/nx)
            
            w = (indQ[k])[0][1] * idf
            Q[indicePalavra] = w
        indicePalavra+=1
    return Q

In [17]:
def verificaConsulta(coords, Q):
    resultado = {}
    Q = Q.reshape((len(Q),1))
    
    for i in range(np.shape(coords)[1]):
        vec = coords[:, i]
        vec = vec.reshape((len(vec),1))
        similaridade = (vec.T @ Q)/(np.linalg.norm(vec) * np.linalg.norm(Q))
        resultado[i] = similaridade[0][0]
    return resultado

In [23]:
print("Lendo arquivos...")

path = "../data"
# path = args.dataset
# Uma linha para o executável, a outra para o ipynb

files = [f for f in glob.glob(path + "**/*", recursive=True)]

#Lê todos os arquivos do dataset e guarda na variável arquivos. Guarda o nome na nome_arquivos
arquivos      = {i:formataString(open(files[i], encoding="latin-1").read()) for i in range(len(files))}
nome_arquivos = [os.path.basename(file) for file in files]

# arquivos = {}

# for file in files:
#     arquivo  = open(file)
#     text     = arquivo.read()
#     filename = os.path.basename(file) 
#     arquivos[filename] = text

Lendo arquivos...


In [24]:
#Tratamento e criação do índice invertido.

# for k, v in arquivos.items():
#     arquivos[k] = formataString(v)
#↑ -> O código abaixo faz o mesmo porém mais rápido
# arquivos = {k:formataString(v) for k,v in arquivos.items()}
print("Tratando arquivos (1/2)...")
indInv = indiceInvertido(arquivos)
print("Tratando arquivos (2/2)...")

coords = coordenadas(indInv, len(arquivos))

Tratando arquivos (1/2)...


{'from': [[0, 2],
  [1, 1],
  [2, 1],
  [3, 3],
  [4, 1],
  [5, 1],
  [6, 6],
  [7, 1],
  [8, 2],
  [9, 1],
  [10, 2],
  [11, 1],
  [12, 4],
  [13, 2],
  [14, 1],
  [15, 1],
  [16, 2],
  [17, 5],
  [18, 2],
  [19, 1],
  [20, 2],
  [21, 1],
  [22, 1],
  [23, 3],
  [24, 2],
  [25, 1],
  [26, 1],
  [27, 2],
  [28, 1],
  [29, 1],
  [30, 2],
  [31, 2],
  [32, 3],
  [33, 3],
  [34, 3],
  [35, 1],
  [36, 1],
  [37, 2],
  [38, 1],
  [39, 2],
  [40, 2],
  [41, 1],
  [42, 1],
  [43, 1],
  [44, 1],
  [45, 2],
  [46, 2],
  [47, 1],
  [48, 1],
  [49, 2],
  [50, 1],
  [51, 2],
  [52, 2],
  [53, 7],
  [54, 1],
  [55, 1],
  [56, 1],
  [57, 1],
  [58, 3],
  [59, 1],
  [60, 3],
  [61, 1],
  [62, 4],
  [63, 2],
  [64, 1],
  [65, 2],
  [66, 1],
  [67, 1],
  [68, 6],
  [69, 2],
  [70, 1],
  [71, 5],
  [72, 1],
  [73, 18],
  [74, 2],
  [75, 1],
  [76, 3],
  [77, 21],
  [78, 1],
  [79, 1],
  [80, 1],
  [81, 1],
  [82, 2],
  [83, 2],
  [84, 1],
  [85, 1],
  [86, 2],
  [87, 1],
  [88, 1],
  [89, 4],
  [90, 2],

In [82]:
consulta = "VHS Tape"
query = {0:formataString(consulta)}
indQ = indiceInvertido(query)

# print(indQ)

Q = formataQuery(indInv, indQ, len(arquivos))

# print(Q)
print("Done!",time.time() - start_time)
resultado = verificaConsulta(coords, Q)
print("Maior valor = maior prioridade:")
# print(resultado)
print("Done!",time.time() - start_time)
for k, v in resultado.items():
    print("Valor para o documento ", nome_arquivos[k], " : ", v)


Done! 261.87508487701416
Maior valor = maior prioridade:
Done! 282.73901414871216
Valor para o documento  54119  :  0.3729674904765139
Valor para o documento  10121  :  0.0
Valor para o documento  76121  :  0.0
Valor para o documento  54331  :  0.0
Valor para o documento  103459  :  0.0
Valor para o documento  179055  :  0.0
Valor para o documento  39632  :  0.0
Valor para o documento  54307  :  0.0
Valor para o documento  53463  :  0.0
Valor para o documento  16115  :  0.0
Valor para o documento  15883  :  0.0
Valor para o documento  76273  :  0.0
Valor para o documento  54510  :  0.0
Valor para o documento  77291  :  0.0
Valor para o documento  76640  :  0.0
Valor para o documento  59485  :  0.0
Valor para o documento  52075  :  0.0
Valor para o documento  77293  :  0.0
Valor para o documento  54077  :  0.0
Valor para o documento  67516  :  0.0
Valor para o documento  68188  :  0.0
Valor para o documento  54780  :  0.0
Valor para o documento  61494  :  0.0
Valor para o documento  772